# **Final LightGBM Model:** Hospital Charge Prediction

In [3]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error
import lightgbm as lgb
import joblib

In [ ]:
df = pd.read_csv('../data/model_input_final_clean.csv')

In [38]:
# Define feature columns
feature_cols = [
    'gender_encoded', 'age_group_encoded', 'severity_encoded',
    'admission_encoded', 'payment_type_encoded', 'diagnosis_encoded',
    'procedure_encoded', 'county_encoded', 'los',
    'los_x_severity', 'los_x_procedure', 'severity_x_procedure', 'los_x_county',
    'diagnosis_x_severity', 'procedure_x_severity', 
    'diagnosis_x_procedure', 'county_x_los'
]

In [39]:
X = df[feature_cols]
y = np.log1p(df['total_charges'])
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [40]:
base_model = lgb.LGBMRegressor(n_estimators=1000, learning_rate=0.05)
base_model.fit(X_train, y_train)

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.022952 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2544
[LightGBM] [Info] Number of data points in the train set: 1873243, number of used features: 17
[LightGBM] [Info] Start training from score 10.142437


LGBMRegressor(learning_rate=0.05, n_estimators=1000)

In [41]:
# Predict and evaluate on the test set
y_pred_log = base_model.predict(X_test)
y_pred = np.expm1(y_pred_log)  # undo the log1p transformation
y_true = np.expm1(y_test)

# Calculate MAE
mae_global = mean_absolute_error(y_true, y_pred)
print(f"Global Model MAE: ${mae_global:,.2f}")

Global Model MAE: $13,057.92


In [43]:
# Add diagnosis group manually
def categorize_diagnosis(desc):
    desc = desc.lower()
    if any(x in desc for x in ['leukemia', 'lymphoma', 'myeloma', 'neoplasm', 'cancer']):
        return 'Oncology'
    elif any(x in desc for x in ['short gestation', 'liveborn', 'fetal', 'newborn', 'neonatal']):
        return 'Neonatal'
    elif any(x in desc for x in ['schizophrenia', 'mood', 'psychotic', 'substance', 'alcohol']):
        return 'Behavioral'
    elif any(x in desc for x in ['septicemia', 'pneumonia', 'infection']):
        return 'Infectious'
    elif any(x in desc for x in ['osteoarthritis', 'spondylosis', 'back problems']):
        return 'Orthopedic'
    elif any(x in desc for x in ['diabetes', 'heart failure', 'dysrhythmia', 'myocardial', 'coronary']):
        return 'Cardio-Metabolic'
    elif any(x in desc for x in ['pregnancy', 'delivery', 'c-section', 'puerperium']):
        return 'OB/GYN'
    else:
        return 'General'

# Load mapping (you need this .csv)
diag_map = pd.read_csv('../data/diagnosis_mapping.csv')

# Merge readable diagnosis names
df = df.merge(diag_map, on='diagnosis_encoded', how='left')

# Create group
df['diagnosis_group'] = df['ccs_diagnosis_description'].apply(categorize_diagnosis)

In [44]:
from collections import defaultdict
import lightgbm as lgb

group_models = {}
group_maes = {}

# Pull distinct groups
groups = df['diagnosis_group'].dropna().unique()

for group in groups:
    group_df = df[df['diagnosis_group'] == group].copy()

    X_group = group_df[feature_cols]
    y_group = np.log1p(group_df['total_charges'])
    X_train, X_test, y_train, y_test = train_test_split(X_group, y_group, random_state=42)
   
    model = lgb.LGBMRegressor(n_estimators=1000, learning_rate=0.05)
    model.fit(X_train, y_train)

    preds = np.expm1(model.predict(X_test))
    y_true = np.expm1(y_test)
    mae = mean_absolute_error(y_true, preds)

    group_models[group] = model
    group_maes[group] = mae

# Show all group MAEs
for group, mae in group_maes.items():
    print(f"{group} MAE: ${mae:,.2f}")

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.009169 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2544
[LightGBM] [Info] Number of data points in the train set: 833469, number of used features: 17
[LightGBM] [Info] Start training from score 10.284842
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001960 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1906
[LightGBM] [Info] Number of data points in the train set: 161873, number of used features: 17
[LightGBM] [Info] Start training from score 10.396232
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001797 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not e

In [45]:
# Start with global model predictions
df['ensemble_prediction'] = np.expm1(base_model.predict(df[feature_cols]))
df['hybrid_prediction'] = df['ensemble_prediction'].copy()

# Baseline MAEs for comparison
original_group_maes = {
    'Oncology': 19382,
    'Orthopedic': 15300,
    'Cardio-Metabolic': 15100,
    'General': 13700,
    'Infectious': 13300,
    'Behavioral': 7600,
    'Neonatal': 5200,
    'OB/GYN': 4400,
}

# Replace with group predictions only where they improve
for group in df['diagnosis_group'].dropna().unique():
    if group in original_group_maes and group_maes[group] < original_group_maes[group]:
        print(f"✅ Using grouped model for {group} (MAE improved)")
        idx = df['diagnosis_group'] == group
        df.loc[idx, 'hybrid_prediction'] = np.expm1(group_models[group].predict(df.loc[idx, feature_cols]))

In [46]:
final_mae = mean_absolute_error(df['total_charges'], df['hybrid_prediction'])
print(f"\n🏁 Final Hybrid Model MAE: ${final_mae:,.2f}")


🏁 Final Hybrid Model MAE: $13,049.32


In [48]:
# Define X and y
X = df[feature_cols]
y = np.log1p(df['total_charges'])  # log-transform target for training

# Train-validation split for tuning
from sklearn.model_selection import train_test_split
X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size=0.2, random_state=42)

In [49]:
import optuna
def objective(trial):
    params = {
        "n_estimators": trial.suggest_int("n_estimators", 500, 2000),
        "learning_rate": trial.suggest_float("learning_rate", 0.01, 0.3, log=True),
        "max_depth": trial.suggest_int("max_depth", 3, 12),
        "num_leaves": trial.suggest_int("num_leaves", 20, 300),
        "min_child_samples": trial.suggest_int("min_child_samples", 5, 100),
        "subsample": trial.suggest_float("subsample", 0.5, 1.0),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.5, 1.0),
        "reg_alpha": trial.suggest_float("reg_alpha", 0.0, 5.0),
        "reg_lambda": trial.suggest_float("reg_lambda", 0.0, 5.0),
        "random_state": 42,
        "n_jobs": -1,
    }

    model = lgb.LGBMRegressor(**params)
    model.fit(X_train, y_train)

    preds = np.expm1(model.predict(X_valid))
    true = np.expm1(y_valid)
    mae = mean_absolute_error(true, preds)
    return mae

In [50]:
study = optuna.create_study(direction="minimize")
study.optimize(objective, n_trials=50)

print("Best MAE:", study.best_value)
print("Best Parameters:", study.best_params)

[I 2025-08-05 23:23:49,019] A new study created in memory with name: no-name-c3f7768a-5c8b-4e65-871b-c4ded9f1318b


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.010759 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2531
[LightGBM] [Info] Number of data points in the train set: 1873243, number of used features: 17
[LightGBM] [Info] Start training from score 10.142437
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best ga

[I 2025-08-05 23:24:11,712] Trial 0 finished with value: 15796.311955832529 and parameters: {'n_estimators': 885, 'learning_rate': 0.012580626130698951, 'max_depth': 4, 'num_leaves': 83, 'min_child_samples': 83, 'subsample': 0.6974600587629703, 'colsample_bytree': 0.5147787808493577, 'reg_alpha': 1.329715990334885, 'reg_lambda': 1.9529126832907784}. Best is trial 0 with value: 15796.311955832529.


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.017169 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2531
[LightGBM] [Info] Number of data points in the train set: 1873243, number of used features: 17
[LightGBM] [Info] Start training from score 10.142437
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best ga

[I 2025-08-05 23:25:38,427] Trial 1 finished with value: 12289.549010091927 and parameters: {'n_estimators': 1818, 'learning_rate': 0.2824995389326457, 'max_depth': 10, 'num_leaves': 247, 'min_child_samples': 72, 'subsample': 0.8435801249345006, 'colsample_bytree': 0.932186145445216, 'reg_alpha': 2.2682553982381344, 'reg_lambda': 1.3671269255080776}. Best is trial 1 with value: 12289.549010091927.


...

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.011655 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2531
[LightGBM] [Info] Number of data points in the train set: 1873243, number of used features: 17
[LightGBM] [Info] Start training from score 10.142437
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf


[I 2025-08-06 00:27:47,266] Trial 48 finished with value: 12544.459317711899 and parameters: {'n_estimators': 1280, 'learning_rate': 0.015712119686297488, 'max_depth': 12, 'num_leaves': 251, 'min_child_samples': 68, 'subsample': 0.8235909698345547, 'colsample_bytree': 0.6585084416075615, 'reg_alpha': 3.0420394720459822, 'reg_lambda': 0.6148182164006577}. Best is trial 36 with value: 12020.217930996154.


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.013111 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2531
[LightGBM] [Info] Number of data points in the train set: 1873243, number of used features: 17
[LightGBM] [Info] Start training from score 10.142437
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best ga

[I 2025-08-06 00:29:22,183] Trial 49 finished with value: 12047.369674419511 and parameters: {'n_estimators': 1746, 'learning_rate': 0.1011762380093266, 'max_depth': 10, 'num_leaves': 273, 'min_child_samples': 58, 'subsample': 0.7786449329510048, 'colsample_bytree': 0.7546018611043213, 'reg_alpha': 2.473721369895843, 'reg_lambda': 1.7904036395754952}. Best is trial 36 with value: 12020.217930996154.


Best MAE: 12020.217930996154
Best Parameters: {'n_estimators': 1874, 'learning_rate': 0.0875403852825351, 'max_depth': 12, 'num_leaves': 265, 'min_child_samples': 61, 'subsample': 0.6745113925252707, 'colsample_bytree': 0.6858714521709702, 'reg_alpha': 3.4299949019901, 'reg_lambda': 1.4416258237066328}


In [51]:
study.best_params

{'n_estimators': 1874,
 'learning_rate': 0.0875403852825351,
 'max_depth': 12,
 'num_leaves': 265,
 'min_child_samples': 61,
 'subsample': 0.6745113925252707,
 'colsample_bytree': 0.6858714521709702,
 'reg_alpha': 3.4299949019901,
 'reg_lambda': 1.4416258237066328}

In [52]:
final_model = lgb.LGBMRegressor(
    n_estimators=1874,
    learning_rate=0.08754,
    max_depth=12,
    num_leaves=265,
    min_child_samples=61,
    subsample=0.6745,
    colsample_bytree=0.68587,
    reg_alpha=3.43,
    reg_lambda=1.44
)

X = df[feature_cols]
y = np.log1p(df['total_charges'])

final_model.fit(X, y)

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.027813 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2540
[LightGBM] [Info] Number of data points in the train set: 2341554, number of used features: 17
[LightGBM] [Info] Start training from score 10.142602
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best ga

LGBMRegressor(colsample_bytree=0.68587, learning_rate=0.08754, max_depth=12,
              min_child_samples=61, n_estimators=1874, num_leaves=265,
              reg_alpha=3.43, reg_lambda=1.44, subsample=0.6745)

In [53]:
df['ensemble_prediction'] = np.expm1(final_model.predict(df[feature_cols]))
df['hybrid_prediction'] = df['ensemble_prediction'].copy()

# Use group models only if they beat the global one
for group in groups:
    if group in original_group_maes and group_maes[group] < original_group_maes[group]:
        idx = df['diagnosis_group'] == group
        df.loc[idx, 'hybrid_prediction'] = np.expm1(group_models[group].predict(df.loc[idx, feature_cols]))

In [ ]:
final_mae = mean_absolute_error(df['total_charges'], df['hybrid_prediction'])
print(f"🔥 FINAL Tuned Hybrid MAE: ${final_mae:,.2f}")

🔥 FINAL Tuned Hybrid MAE: $11,137.83


In [60]:
group_mae_breakdown = (
    df.groupby('diagnosis_group')
    .apply(lambda g: mean_absolute_error(g['total_charges'], g['hybrid_prediction']))
    .sort_values()
)
print(group_mae_breakdown)

diagnosis_group
OB/GYN               4505.594751
Neonatal             5180.389313
Behavioral           7276.255043
General             12001.262439
Infectious          12608.863178
Cardio-Metabolic    14336.610960
Orthopedic          15438.044042
Oncology            18496.106313
dtype: float64


/var/folders/6z/l9wv3crd4n5bzgcrdd7vxq8m0000gn/T/ipykernel_21174/1955162874.py:3: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  .apply(lambda g: mean_absolute_error(g['total_charges'], g['hybrid_prediction']))


In [ ]:
# import joblib
# joblib.dump(final_model, '../models/final_tuned_lgbm.joblib')

['../models/final_tuned_lgbm.joblib']

## Integrate LOS Models

In [ ]:
# Add interaction features
df['los_x_severity'] = df['los'] * df['severity_encoded']
df['los_x_procedure'] = df['los'] * df['procedure_encoded']
df['severity_x_procedure'] = df['severity_encoded'] * df['procedure_encoded']
df['los_x_county'] = df['los'] * df['county_encoded']

interaction_features = ['los_x_severity', 'los_x_procedure', 'severity_x_procedure', 'los_x_county']
feature_cols = list(dict.fromkeys(feature_cols + interaction_features))

In [56]:
df['los_group'] = pd.cut(
    df['los'],
    bins=[0, 3, 7, 14, df['los'].max()],
    labels=['short', 'moderate', 'long', 'extended'],
    right=True
)

In [68]:
# Latest 17-feature list
X = df[feature_cols]
y = np.log1p(df['total_charges'])

# Train/test split per LOS group
models = {}
for group in ['short', 'moderate', 'long', 'extended']:
    group_df = df[df['los_group'] == group]
    X_group = group_df[feature_cols]
    y_group = np.log1p(group_df['total_charges'])

    X_train, X_test, y_train, y_test = train_test_split(X_group, y_group, test_size=0.2, random_state=42)
    
    model = lgb.LGBMRegressor(random_state=42)
    model.fit(X_train, y_train)
    models[group] = model

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.010165 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1907
[LightGBM] [Info] Number of data points in the train set: 1055228, number of used features: 17
[LightGBM] [Info] Start training from score 9.650624
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.006562 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2061
[LightGBM] [Info] Number of data points in the train set: 489844, number of used features: 17
[LightGBM] [Info] Start training from score 10.425097
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.003260 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not e

In [73]:
model_s = joblib.load("../models/model_short.pkl")
model_m = joblib.load("../models/model_moderate.pkl")
model_l = joblib.load("../models/model_long.pkl")
model_e = joblib.load("../models/model_extended.pkl")

In [74]:
los_mae = {
    'short': 7274,
    'moderate': 13135,
    'long': 23670,
    'extended': 60464
}

# If you already have this column
df['los_group'] = df['los_group'].astype(str)

# Create hybrid prediction column
df['los_hybrid_prediction'] = df['ensemble_prediction']

# Override predictions
for group, model in zip(
    ['short', 'moderate', 'long', 'extended'],
    [model_s, model_m, model_l, model_e]
):
    if los_mae[group] < mae_global:  # only override if better
        idx = df['los_group'] == group
        df.loc[idx, 'los_hybrid_prediction'] = np.expm1(
            model.predict(df.loc[idx, feature_cols])
        )

In [ ]:
final_los_mae = mean_absolute_error(df['total_charges'], df['los_hybrid_prediction'])
print(f"📊 Final LOS-Segmented Hybrid MAE: ${final_los_mae:,.2f}")

📊 Final LOS-Segmented Hybrid MAE: $11,921.74


In [77]:
def tune_los_group(df, group, feature_cols):
    from sklearn.model_selection import train_test_split
    from sklearn.metrics import mean_absolute_error
    import optuna
    import lightgbm as lgb
    import numpy as np

    # Subset group
    group_df = df[df['los_group'] == group]
    X = group_df[feature_cols]
    y = np.log1p(group_df['total_charges'])
    X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size=0.2, random_state=42)

    def objective(trial):
        params = {
            'n_estimators': trial.suggest_int('n_estimators', 300, 2000),
            'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3, log=True),
            'max_depth': trial.suggest_int('max_depth', 3, 12),
            'num_leaves': trial.suggest_int('num_leaves', 20, 300),
            'min_child_samples': trial.suggest_int('min_child_samples', 5, 100),
            'subsample': trial.suggest_float('subsample', 0.5, 1.0),
            'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
            'reg_alpha': trial.suggest_float('reg_alpha', 0.0, 5.0),
            'reg_lambda': trial.suggest_float('reg_lambda', 0.0, 5.0),
            'random_state': 42
        }

        model = lgb.LGBMRegressor(**params)
        model.fit(X_train, y_train)
        preds = np.expm1(model.predict(X_valid))
        true = np.expm1(y_valid)
        return mean_absolute_error(true, preds)

    study = optuna.create_study(direction='minimize')
    study.optimize(objective, n_trials=50)

    return study.best_params, study.best_value

In [78]:
los_groups = ['short', 'moderate', 'long', 'extended']
los_best_params = {}
los_best_maes = {}

for group in los_groups:
    print(f"Tuning LightGBM model for LOS group: {group}...")
    best_params, best_mae = tune_los_group(df, group, feature_cols)
    los_best_params[group] = best_params
    los_best_maes[group] = best_mae
    print(f"✅ Best MAE for {group}: ${best_mae:,.2f}\n")
        

Tuning LightGBM model for LOS group: short...


[I 2025-08-06 11:25:54,066] A new study created in memory with name: no-name-e54c40ce-c3e9-45a8-8d3f-78b8c397fe8e


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.011218 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1907
[LightGBM] [Info] Number of data points in the train set: 1055228, number of used features: 17
[LightGBM] [Info] Start training from score 9.650624
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf


[I 2025-08-06 11:26:35,726] Trial 0 finished with value: 6660.46245648176 and parameters: {'n_estimators': 1684, 'learning_rate': 0.013009964099528253, 'max_depth': 9, 'num_leaves': 61, 'min_child_samples': 61, 'subsample': 0.6821014262085485, 'colsample_bytree': 0.5607724972815791, 'reg_alpha': 1.1623032623938456, 'reg_lambda': 4.969271100682128}. Best is trial 0 with value: 6660.46245648176.


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.009690 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1907
[LightGBM] [Info] Number of data points in the train set: 1055228, number of used features: 17
[LightGBM] [Info] Start training from score 9.650624


...

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001645 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2517
[LightGBM] [Info] Number of data points in the train set: 119393, number of used features: 17
[LightGBM] [Info] Start training from score 11.777569
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gai

[I 2025-08-06 12:25:53,153] Trial 48 finished with value: 53862.93106682092 and parameters: {'n_estimators': 596, 'learning_rate': 0.23752944879463983, 'max_depth': 6, 'num_leaves': 212, 'min_child_samples': 62, 'subsample': 0.8301003445924383, 'colsample_bytree': 0.8432588991300615, 'reg_alpha': 2.610158638963009, 'reg_lambda': 2.178306493300614}. Best is trial 42 with value: 53171.12320469484.


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001144 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2517
[LightGBM] [Info] Number of data points in the train set: 119393, number of used features: 17
[LightGBM] [Info] Start training from score 11.777569
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gai

[I 2025-08-06 12:25:59,278] Trial 49 finished with value: 53068.93231451329 and parameters: {'n_estimators': 1071, 'learning_rate': 0.06590358582063928, 'max_depth': 9, 'num_leaves': 111, 'min_child_samples': 18, 'subsample': 0.6052649327153989, 'colsample_bytree': 0.5311271067476651, 'reg_alpha': 0.7934513797061227, 'reg_lambda': 2.6495754360565464}. Best is trial 49 with value: 53068.93231451329.


✅ Best MAE for extended: $53,068.93



In [79]:
los_models = {}

for group in los_groups:
    print(f"Training final model for: {group}")
    group_df = df[df['los_group'] == group]
    X_group = group_df[feature_cols]
    y_group = np.log1p(group_df['total_charges'])

    model = lgb.LGBMRegressor(**los_best_params[group])
    model.fit(X_group, y_group)
    los_models[group] = model

Training final model for: short
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.018740 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1918
[LightGBM] [Info] Number of data points in the train set: 1319035, number of used features: 17
[LightGBM] [Info] Start training from score 9.649752
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further spl

In [80]:
import joblib

joblib.dump(los_models['short'], '../models/tuned_model_short.pkl')
joblib.dump(los_models['moderate'], '../models/tuned_model_moderate.pkl')
joblib.dump(los_models['long'], '../models/tuned_model_long.pkl')
joblib.dump(los_models['extended'], '../models/tuned_model_extended.pkl')

['../models/tuned_model_extended.pkl']

In [81]:
df['los_hybrid_prediction'] = df['ensemble_prediction']

for group in los_groups:
    if los_best_maes[group] < mae_global:
        idx = df['los_group'] == group
        df.loc[idx, 'los_hybrid_prediction'] = np.expm1(
            los_models[group].predict(df.loc[idx, feature_cols])
        )

In [82]:
final_mae = mean_absolute_error(df['total_charges'], df['los_hybrid_prediction'])
print(f"🔥 FINAL Tuned LOS-Segmented Hybrid MAE: ${final_mae:,.2f}")

🔥 FINAL Tuned LOS-Segmented Hybrid MAE: $11,027.50
